![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo P 2013 Alimentação

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [ ]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA>")

## Definição do peso e filtragem de respondentes do questionario

In [3]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2013.1<-pns2013 %>% filter(M001==1)
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
#Desfechos - Indicadores

#Indivíduos de 18 anos ou mais que consomem feijão regularmente  - P001P
pns2013.1 <- pns2013.1 %>% filter(P006!=9) %>% mutate(P001P = ifelse(P006>=5, 1,2))
pns2013.1$P001P<-factor(pns2013.1$P001P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P001P)

#Indivíduos de 18 anos ou mais com consumo adequado de frutas, legumes e verduras - P002P
pns2013.1 <- pns2013.1 %>% mutate(P002P = if_else(P007 >= 5 & P018>=5,1,
                                          if_else(P009 >= 5 & P018>=5,1,2,missing=2),missing=2))                                         
pns2013.1$P002P<-factor(pns2013.1$P002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$P002P)


#Indivíduos de 18 anos ou mais que consomem peixe pelo menos um dia por semana  - P003P
pns2013.1 <- pns2013.1 %>% filter(P015!=9) %>% mutate(P003P = ifelse(P015>=1, 1,2))
pns2013.1$P003P<-factor(pns2013.1$P003P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P003P)


#Indivíduos de 18 anos ou mais que consomem refrigerantes regularmente  - P004P
pns2013.1 <- pns2013.1 %>% filter(P020!=9) %>% mutate(P004P = ifelse(P020>=5, 1,2))
pns2013.1$P004P<-factor(pns2013.1$P004P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P004P)

#Indivíduos de 18 anos ou mais que consomem alimentos doces regularmente  - P005P
pns2013.1 <- pns2013.1 %>% filter(P025!=9) %>% mutate(P005P = ifelse(P025>=5, 1,2))
pns2013.1$P005P<-factor(pns2013.1$P005P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P005P)

#Indivíduos de 18 anos ou mais que substituem o almoço por sanduiches, salgados ou pizzas regularmente  - P006P
pns2013.1 <- pns2013.1 %>% filter(P026!=9) %>% mutate(P006P = ifelse(P026>=5, 1,2))
pns2013.1$P006P<-factor(pns2013.1$P006P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P006P)

#Indivíduos de 18 anos ou mais que referem consumo elevado de sal - P007P
pns2013.1 <- pns2013.1 %>% filter(P02601!=9) %>% mutate(P007P = ifelse(P02601==1|P02601==2, 1,2))
pns2013.1$P007P<-factor(pns2013.1$P007P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P007P)



Sim   Nao 
40489 19713

Sim   Não 
16367 43835

Sim   Nao 
36168 24034

Sim   Nao 
13088 47114

Sim   Nao 
11262 48940

Sim   Nao 
 3457 56745

Sim   Nao 
 8188 52014

## Definições de abrangências

### Situação urbana ou rural

In [72]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2013.1$Sit_Urbano_Rural)

Urbano  Rural 
 49245  10957

### Sexo

In [73]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [74]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondonia","Acre","Amazonas","Roraima","Para","Amapa","Tocantins","Maranhao","Piaui","Ceara",
                                        "Rio Grande do Norte","Paraiba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espirito Santo","Rio de Janeiro","Sao Paulo",
                                        "Parana","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goias","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondonia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Para               Amapa           Tocantins            Maranhao 
               2004                1332                1515                1774 
              Piaui               Ceara Rio Grande do Norte             Paraiba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espirito Santo      Rio de Janeiro           Sao Paulo 
               3779                1724                3486                5305 
             Parana      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goias    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [75]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `1 Norte` = c("Rondonia","Acre","Amazonas","Roraima","Para", "Amapa","Tocantins"),
                                          `2 Nordeste` = c("Maranhao", "Piaui", "Ceara", "Rio Grande do Norte", "Paraiba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `3 Sudeste` = c("Minas Gerais", "Espirito Santo","Rio de Janeiro", "Sao Paulo"), 
                                          `4 Sul` = c("Parana", "Santa Catarina", "Rio Grande do Sul"),
                                          `5 Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goias", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

1 Norte     2 Nordeste      3 Sudeste          4 Sul 5 Centro-Oeste 
         12536          18305          14294           7548           7519

### Capital

In [76]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondonia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco `= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Boa Vista`= "Roraima",
                                        `Belem` = "Para" ,
                                        `Macapa`= "Amapa",
                                        `Palmas` = "Tocantins",
                                        `Sao Luis` = "Maranhao",
                                        `Teresina`= "Piaui" ,
                                        `Fortaleza`= "Ceara",
                                        `Natal`= "Rio Grande do Norte",
                                        `Joao Pessoa`= "Paraiba",
                                        `Recife`= "Pernambuco",
                                        `Maceio`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitoria`= "Espirito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `Sao Paulo`= "Sao Paulo",
                                        `Curitiba`= "Parana",
                                        `Florianopolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiaba`= "Mato Grosso",
                                        `Goiania` = "Goias",
                                        `Brasilia`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho    Rio Branco          Manaus      Boa Vista          Belem 
          1694           1814           2586           1591           2004 
        Macapa         Palmas       Sao Luis       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    Joao Pessoa         Recife         Maceio        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitoria Rio de Janeiro      Sao Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianopolis   Porto Alegre   Campo Grande         Cuiaba 
          3012           1623           2913           1809           1476 
       Goiania       Brasilia 
          2423           1811

### Faixa Etária

In [77]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          14321           20242           14462            8290            2887

### Raça

In [78]:
#Raça
pns2013.1 <- pns2013.1 %>% filter(C009!=3|C009!=5|C009!=9)%>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2 , 2, 3)))
pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2013.1$Raca)

Branca  Preta  Parda 
 24106   5631  30465

### Renda per capita

In [79]:
#Rendimento domiciliar per capita

pns2013.1 <-  pns2013.1 %>% drop_na(VDF003) %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Ate 1/2 SM","1/2 ate 1 SM","1 ate 2 SM","2 ate 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)


Ate 1/2 SM 1/2 ate 1 SM   1 ate 2 SM   2 ate 3 SM Mais de 3 SM 
       14256        17504        15493         5335         7603

### Escolaridade

In [80]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Sem instrucao e fundamental incompleto","Fundamental completo e medio incompleto",
                                           "Medio completo e superior incompleto","Superior completo"))
summary(pns2013.1$gescol)

Sem instrucao e fundamental incompleto Fundamental completo e medio incompleto 
                                  24080                                    9212 
   Medio completo e superior incompleto                       Superior completo 
                                  19145                                    7754

## Criando indicadores

### Filtrando base de indicadores

In [81]:
#Selecionando variáveis para cálculo de indicadores no survey_ALTERAR
pns2013Psurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "P001P","P002P","P003P","P004P", "P005P","P006P","P007P",
                                     "C008","V0031","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita","gescol")
summary(pns2013Psurvey)

     V0024            UPA_PNS        peso_morador_selec  P001P      
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Sim:40485  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243935   Nao:19706  
 Median :2951023   Median :2900192   Median : 0.521557              
 Mean   :3035304   Mean   :3007768   Mean   : 1.000020              
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147380              
 Max.   :5310220   Max.   :5300180   Max.   :31.179597              
                                                                    
 P002P       P003P       P004P       P005P       P006P       P007P      
 Sim:16361   Sim:36160   Sim:13086   Sim:11261   Sim: 3454   Sim: 8185  
 Não:43830   Nao:24031   Nao:47105   Nao:48930   Nao:56737   Nao:52006  
                                                                        
                                                                        
                                                                        
          

### Exporta tabela filtrada

In [82]:
#Salvando csv para cálculo de indicadores no survey_ALTERAR
path <- "<coloque aqui o caminho onde deseja salvar a base filtrada>"
write.csv(pns2013Psurvey, file.path(path, "pns2013Psurvey.csv"))

### Cria plano amostral complexo

In [83]:
#survey design
desPNSP=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Psurvey)
desPNSP18=subset(desPNSP, C008>=18)
desPNSPC=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Psurvey)
desPNSPC18=subset(desPNSPC, C008>=18 & V0031==1)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [84]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [85]:
ListaIndicadores = c(~P001P,~P002P,~P003P,~P004P,~P005P,~P006P,~P007P)
ListaIndicadoresTexto = c("P001P","P002P","P003P","P004P","P005P","P006P","P007P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("Sexo","raca","rend_per_capita","fx_idade_18","urb_rur","uf","regiao","capital","gescol")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [86]:
#Cálculo dos indicadores usando o pacote survey - alterar
i <- 0
for(indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
              if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSPC18 , svymean,vartype=c("ci","cv"))
               }else{
                    dataframe_indicador<-svyby( indicador , dominio , desPNSP18 , svymean,vartype=c("ci","cv"))
               }
               dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Não","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}


#### Criando a tabela pela abrangência total

In [88]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [89]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        dataframe_indicador_N <- data.frame()
        if(total == 'Capital'){
            dataframe_indicador <- svymean(indicador,desPNSPC18)
        }else{
            dataframe_indicador <- svymean(indicador,desPNSP18)
        }
        
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(confint(dataframe_indicador)))
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..') 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
        dataframe_indicador_N <- dataframe_indicador %>% 
                                 slice(2)
        dataframe_indicador <- cbind(dataframe_indicador_S,dataframe_indicador_N)
        colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','Não','LowerN','UpperN')
        dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','Não','LowerS','LowerN','UpperS','UpperN')
        dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
        print(ListaIndicadoresTexto[i])
        dataframe_indicador$abr_tipo <- "total"
        dataframe_indicador$abr_nome <- total
        dataframe_indicador$Ano <- "2013" 
        print(colnames(dataframe_indicador))
        dataframe_indicador <- dataframe_indicador %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","Não","LowerS","LowerN","UpperS","UpperN")
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador)
        
    }
}


[1] "P001P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P001P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P002P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P002P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P003P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P003P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P004P"
 [1] "Sim"       "Não"       "LowerS"    "LowerN"    "UpperS"    "UpperN"   
 [7] "Indicador" "abr_tipo"  "abr_nome"  "Ano"      
[1] "P

#### Unindo tabela de indicadores e de totais

In [91]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Exportando tabela de indicadores

In [93]:
write.table(matrizIndicadores,file="<coloque aqui o caminho para exportação da matriz de indicadores>",sep = ";",dec = ",",row.names = FALSE)